In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pgeocode as pg #處理 postal code

# Data cleaning

In [4]:
original_data = pd.read_csv('NTHU data v2 w: volume.csv')
original_data

Shipment ID      vendor_name fc_code      type  \
0      FBA18WF7Q4K2    Two's Company    ICT2  DOMESTIC   
1      FBA18W2KGXCR        R&R Corp.    TMB8  DOMESTIC   
2      FBA18VXT1KL7  Glimmer Goddess    TMB8  DOMESTIC   
3      FBA18VSDFCLL          Pet Lou    SCK8  DOMESTIC   
4      FBA18VXNQZY7  Glimmer Goddess    TMB8  DOMESTIC   
...             ...              ...     ...       ...   
58655  FBA15L4PGGQD            Roman    MDW2  DOMESTIC   
58656  FBA15L4S2LRV            Roman    MDW2  DOMESTIC   
58657  FBA15L4NP43H            Roman    MDW2  DOMESTIC   
58658  FBA15L4NP2GJ            Roman    MDW2  DOMESTIC   
58659  FBA15L4NZ6V1            Roman    MDW2  DOMESTIC   

                  ship_method             BM       date  \
0                  AMAZON_LTL       Sally Wu  27-Apr-25   
1      HOUR_LOOP_FEDEX_PARCEL     Ellie Chen  25-Apr-25   
2      HOUR_LOOP_FEDEX_PARCEL    Leona Chang  25-Apr-25   
3      HOUR_LOOP_FEDEX_PARCEL       Sally Wu  25-Apr-25   
4      HOUR_LOOP_FEDEX_PARCEL    Leona Chang  25-Apr-25   
...                       ...            ...        ...   
58655              AMAZON_LTL  Jessica Huang  12-Jul-05   
58656              AMAZON_LTL  Jessica Huang  12-Jul-05   
58657              AMAZON_LTL  Jessica Huang  12-Jul-05   
58658              AMAZON_LTL  Jessica Huang  12-Jul-05   
58659              AMAZON_LTL  Jessica Huang  12-Jul-05   

      Shipping Cost Major Type from_state  from_address_id  \
0                     DOMESTIC         NY             87.0   
1                     DOMESTIC         MD           1858.0   
2                     DOMESTIC         TX          34073.0   
3                     DOMESTIC         CA           6035.0   
4                     DOMESTIC         TX          34073.0   
...                        ...        ...              ...   
58655                 DOMESTIC        NaN              NaN   
58656                 DOMESTIC        NaN              NaN   
58657                 DOMESTIC        NaN              NaN   
58658                 DOMESTIC        NaN              NaN   
58659                 DOMESTIC        NaN              NaN   

       total_vendor_price from_postal_code  amount  weight      $/lb  \
0                 9941.34            10523  438.18  1102.0  0.397623   
1                 2239.92            20852  153.42   277.0  0.553863   
2                 1060.32            75033   30.80    44.0  0.700000   
3                 1685.40            91761  337.96   489.0  0.691125   
4                 5028.00            75033  143.52   205.0  0.700098   
...                   ...              ...     ...     ...       ...   
58655                 NaN              NaN   83.65  2070.0  0.040411   
58656                 NaN              NaN   78.59  1945.0  0.040406   
58657                 NaN              NaN   61.82  1530.0  0.040405   
58658                 NaN              NaN   70.92  1755.0  0.040410   
58659                 NaN              NaN   70.51  1745.0  0.040407   

      esti_dimensional_volume  
0                 322371.8373  
1                 12838.13356  
2                 1996.951518  
3                 188501.4466  
4                 15855.06138  
...                       ...  
58655             399124.7783  
58656             323510.0053  
58657              315711.406  
58658             310488.0743  
58659              284252.999  

[58660 rows x 16 columns]

### 拿掉不重要的變數

In [64]:
data = original_data.dropna(subset = ['Shipment ID'])
data = data[data['type'] == 'DOMESTIC']
data = data[data['ship_method'] != 'VENDOR_LTL']
data = data[data['amount'] > 0]
data

Shipment ID      vendor_name fc_code      type  \
0      FBA18WF7Q4K2    Two's Company    ICT2  DOMESTIC   
1      FBA18W2KGXCR        R&R Corp.    TMB8  DOMESTIC   
2      FBA18VXT1KL7  Glimmer Goddess    TMB8  DOMESTIC   
3      FBA18VSDFCLL          Pet Lou    SCK8  DOMESTIC   
4      FBA18VXNQZY7  Glimmer Goddess    TMB8  DOMESTIC   
...             ...              ...     ...       ...   
58655  FBA15L4PGGQD            Roman    MDW2  DOMESTIC   
58656  FBA15L4S2LRV            Roman    MDW2  DOMESTIC   
58657  FBA15L4NP43H            Roman    MDW2  DOMESTIC   
58658  FBA15L4NP2GJ            Roman    MDW2  DOMESTIC   
58659  FBA15L4NZ6V1            Roman    MDW2  DOMESTIC   

                  ship_method             BM       date  \
0                  AMAZON_LTL       Sally Wu  27-Apr-25   
1      HOUR_LOOP_FEDEX_PARCEL     Ellie Chen  25-Apr-25   
2      HOUR_LOOP_FEDEX_PARCEL    Leona Chang  25-Apr-25   
3      HOUR_LOOP_FEDEX_PARCEL       Sally Wu  25-Apr-25   
4      HOUR_LOOP_FEDEX_PARCEL    Leona Chang  25-Apr-25   
...                       ...            ...        ...   
58655              AMAZON_LTL  Jessica Huang  12-Jul-05   
58656              AMAZON_LTL  Jessica Huang  12-Jul-05   
58657              AMAZON_LTL  Jessica Huang  12-Jul-05   
58658              AMAZON_LTL  Jessica Huang  12-Jul-05   
58659              AMAZON_LTL  Jessica Huang  12-Jul-05   

      Shipping Cost Major Type from_state  from_address_id  \
0                     DOMESTIC         NY             87.0   
1                     DOMESTIC         MD           1858.0   
2                     DOMESTIC         TX          34073.0   
3                     DOMESTIC         CA           6035.0   
4                     DOMESTIC         TX          34073.0   
...                        ...        ...              ...   
58655                 DOMESTIC        NaN              NaN   
58656                 DOMESTIC        NaN              NaN   
58657                 DOMESTIC        NaN              NaN   
58658                 DOMESTIC        NaN              NaN   
58659                 DOMESTIC        NaN              NaN   

       total_vendor_price from_postal_code  amount  weight      $/lb  \
0                 9941.34            10523  438.18  1102.0  0.397623   
1                 2239.92            20852  153.42   277.0  0.553863   
2                 1060.32            75033   30.80    44.0  0.700000   
3                 1685.40            91761  337.96   489.0  0.691125   
4                 5028.00            75033  143.52   205.0  0.700098   
...                   ...              ...     ...     ...       ...   
58655                 NaN              NaN   83.65  2070.0  0.040411   
58656                 NaN              NaN   78.59  1945.0  0.040406   
58657                 NaN              NaN   61.82  1530.0  0.040405   
58658                 NaN              NaN   70.92  1755.0  0.040410   
58659                 NaN              NaN   70.51  1745.0  0.040407   

      esti_dimensional_volume  
0                 322371.8373  
1                 12838.13356  
2                 1996.951518  
3                 188501.4466  
4                 15855.06138  
...                       ...  
58655             399124.7783  
58656             323510.0053  
58657              315711.406  
58658             310488.0743  
58659              284252.999  

[51619 rows x 16 columns]

In [49]:
print(data['type'].value_counts())
print()
print(data['Shipping Cost Major Type'].value_counts())

type
DOMESTIC    51619
Name: count, dtype: int64

Shipping Cost Major Type
DOMESTIC    51619
Name: count, dtype: int64


In [65]:
#後來發現剩下欄位中 type 與 shipping cost major type 皆為 DOMESTIC -> 直接拿掉這些欄位
del data['type']
del data['Shipping Cost Major Type']
del data['BM']  #辦公室政治，不討論效果
data

Shipment ID      vendor_name fc_code             ship_method  \
0      FBA18WF7Q4K2    Two's Company    ICT2              AMAZON_LTL   
1      FBA18W2KGXCR        R&R Corp.    TMB8  HOUR_LOOP_FEDEX_PARCEL   
2      FBA18VXT1KL7  Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
3      FBA18VSDFCLL          Pet Lou    SCK8  HOUR_LOOP_FEDEX_PARCEL   
4      FBA18VXNQZY7  Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
...             ...              ...     ...                     ...   
58655  FBA15L4PGGQD            Roman    MDW2              AMAZON_LTL   
58656  FBA15L4S2LRV            Roman    MDW2              AMAZON_LTL   
58657  FBA15L4NP43H            Roman    MDW2              AMAZON_LTL   
58658  FBA15L4NP2GJ            Roman    MDW2              AMAZON_LTL   
58659  FBA15L4NZ6V1            Roman    MDW2              AMAZON_LTL   

            date from_state  from_address_id  total_vendor_price  \
0      27-Apr-25         NY             87.0             9941.34   
1      25-Apr-25         MD           1858.0             2239.92   
2      25-Apr-25         TX          34073.0             1060.32   
3      25-Apr-25         CA           6035.0             1685.40   
4      25-Apr-25         TX          34073.0             5028.00   
...          ...        ...              ...                 ...   
58655  12-Jul-05        NaN              NaN                 NaN   
58656  12-Jul-05        NaN              NaN                 NaN   
58657  12-Jul-05        NaN              NaN                 NaN   
58658  12-Jul-05        NaN              NaN                 NaN   
58659  12-Jul-05        NaN              NaN                 NaN   

      from_postal_code  amount  weight      $/lb esti_dimensional_volume  
0                10523  438.18  1102.0  0.397623             322371.8373  
1                20852  153.42   277.0  0.553863             12838.13356  
2                75033   30.80    44.0  0.700000             1996.951518  
3                91761  337.96   489.0  0.691125             188501.4466  
4                75033  143.52   205.0  0.700098             15855.06138  
...                ...     ...     ...       ...                     ...  
58655              NaN   83.65  2070.0  0.040411             399124.7783  
58656              NaN   78.59  1945.0  0.040406             323510.0053  
58657              NaN   61.82  1530.0  0.040405              315711.406  
58658              NaN   70.92  1755.0  0.040410             310488.0743  
58659              NaN   70.51  1745.0  0.040407              284252.999  

[51619 rows x 13 columns]

### 儲存簡易資料（無地理資訊）

In [66]:
data['date'] = pd.to_datetime(data['date'])
#data['from_state'] = data['from_state'].fillna('NA')
data = data.dropna(subset = ['weight', '$/lb']) #Original 'NA' means "Not America"
data = data.reset_index(drop = True)
data

/var/folders/rb/3tb3l22x2tgfhls9_hdg4r6h0000gn/T/ipykernel_85337/3781397675.py:1: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  data['date'] = pd.to_datetime(data['date'])


Shipment ID      vendor_name fc_code             ship_method  \
0      FBA18WF7Q4K2    Two's Company    ICT2              AMAZON_LTL   
1      FBA18W2KGXCR        R&R Corp.    TMB8  HOUR_LOOP_FEDEX_PARCEL   
2      FBA18VXT1KL7  Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
3      FBA18VSDFCLL          Pet Lou    SCK8  HOUR_LOOP_FEDEX_PARCEL   
4      FBA18VXNQZY7  Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
...             ...              ...     ...                     ...   
51177  FBA15L4PGGQD            Roman    MDW2              AMAZON_LTL   
51178  FBA15L4S2LRV            Roman    MDW2              AMAZON_LTL   
51179  FBA15L4NP43H            Roman    MDW2              AMAZON_LTL   
51180  FBA15L4NP2GJ            Roman    MDW2              AMAZON_LTL   
51181  FBA15L4NZ6V1            Roman    MDW2              AMAZON_LTL   

            date from_state  from_address_id  total_vendor_price  \
0     2025-04-27         NY             87.0             9941.34   
1     2025-04-25         MD           1858.0             2239.92   
2     2025-04-25         TX          34073.0             1060.32   
3     2025-04-25         CA           6035.0             1685.40   
4     2025-04-25         TX          34073.0             5028.00   
...          ...        ...              ...                 ...   
51177 2005-07-12        NaN              NaN                 NaN   
51178 2005-07-12        NaN              NaN                 NaN   
51179 2005-07-12        NaN              NaN                 NaN   
51180 2005-07-12        NaN              NaN                 NaN   
51181 2005-07-12        NaN              NaN                 NaN   

      from_postal_code  amount  weight      $/lb esti_dimensional_volume  
0                10523  438.18  1102.0  0.397623             322371.8373  
1                20852  153.42   277.0  0.553863             12838.13356  
2                75033   30.80    44.0  0.700000             1996.951518  
3                91761  337.96   489.0  0.691125             188501.4466  
4                75033  143.52   205.0  0.700098             15855.06138  
...                ...     ...     ...       ...                     ...  
51177              NaN   83.65  2070.0  0.040411             399124.7783  
51178              NaN   78.59  1945.0  0.040406             323510.0053  
51179              NaN   61.82  1530.0  0.040405              315711.406  
51180              NaN   70.92  1755.0  0.040410             310488.0743  
51181              NaN   70.51  1745.0  0.040407              284252.999  

[51182 rows x 13 columns]

In [52]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51182 entries, 0 to 51181
Data columns (total 13 columns):
 #   Column                   Non-Null Count  Dtype         
---  ------                   --------------  -----         
 0   Shipment ID              51182 non-null  object        
 1   vendor_name              51182 non-null  object        
 2   fc_code                  51182 non-null  object        
 3   ship_method              51182 non-null  object        
 4   date                     51182 non-null  datetime64[ns]
 5   from_state               32037 non-null  object        
 6   from_address_id          32046 non-null  float64       
 7   total_vendor_price       23654 non-null  float64       
 8   from_postal_code         32046 non-null  object        
 9   amount                   51182 non-null  float64       
 10  weight                   51182 non-null  float64       
 11  $/lb                     51182 non-null  float64       
 12  esti_dimensional_volume  51182 n

In [53]:
data1 = data[['Shipment ID', 'vendor_name', 'fc_code', 'ship_method',
               'date', 'weight', 'esti_dimensional_volume', 'amount', '$/lb']]
data1.columns = ['Shipment ID', 'vendor_name', 'fc_code', 'ship_method',
                 'date', 'weight', 'volume', 'cost', '$/lb']
data1

Shipment ID      vendor_name fc_code             ship_method  \
0      FBA18WF7Q4K2    Two's Company    ICT2              AMAZON_LTL   
1      FBA18W2KGXCR        R&R Corp.    TMB8  HOUR_LOOP_FEDEX_PARCEL   
2      FBA18VXT1KL7  Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
3      FBA18VSDFCLL          Pet Lou    SCK8  HOUR_LOOP_FEDEX_PARCEL   
4      FBA18VXNQZY7  Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
...             ...              ...     ...                     ...   
51177  FBA15L4PGGQD            Roman    MDW2              AMAZON_LTL   
51178  FBA15L4S2LRV            Roman    MDW2              AMAZON_LTL   
51179  FBA15L4NP43H            Roman    MDW2              AMAZON_LTL   
51180  FBA15L4NP2GJ            Roman    MDW2              AMAZON_LTL   
51181  FBA15L4NZ6V1            Roman    MDW2              AMAZON_LTL   

            date  weight       volume    cost      $/lb  
0     2025-04-27  1102.0  322371.8373  438.18  0.397623  
1     2025-04-25   277.0  12838.13356  153.42  0.553863  
2     2025-04-25    44.0  1996.951518   30.80  0.700000  
3     2025-04-25   489.0  188501.4466  337.96  0.691125  
4     2025-04-25   205.0  15855.06138  143.52  0.700098  
...          ...     ...          ...     ...       ...  
51177 2005-07-12  2070.0  399124.7783   83.65  0.040411  
51178 2005-07-12  1945.0  323510.0053   78.59  0.040406  
51179 2005-07-12  1530.0   315711.406   61.82  0.040405  
51180 2005-07-12  1755.0  310488.0743   70.92  0.040410  
51181 2005-07-12  1745.0   284252.999   70.51  0.040407  

[51182 rows x 9 columns]

In [54]:
data1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51182 entries, 0 to 51181
Data columns (total 9 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   Shipment ID  51182 non-null  object        
 1   vendor_name  51182 non-null  object        
 2   fc_code      51182 non-null  object        
 3   ship_method  51182 non-null  object        
 4   date         51182 non-null  datetime64[ns]
 5   weight       51182 non-null  float64       
 6   volume       51182 non-null  object        
 7   cost         51182 non-null  float64       
 8   $/lb         51182 non-null  float64       
dtypes: datetime64[ns](1), float64(3), object(5)
memory usage: 3.5+ MB


In [104]:
data1 = data1[data1['volume']!='#NUM!']
data1['log_cost'] = np.log1p(data1['cost'])
data1['log_weight'] = np.log1p(data1['weight'])
data1['volume'] = data1['volume'].astype(float)
data1['log_volume'] = np.log1p(data1['volume'])
data1

/var/folders/rb/3tb3l22x2tgfhls9_hdg4r6h0000gn/T/ipykernel_85337/2755088573.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data1['log_cost'] = np.log1p(data1['cost'])
/var/folders/rb/3tb3l22x2tgfhls9_hdg4r6h0000gn/T/ipykernel_85337/2755088573.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data1['log_weight'] = np.log1p(data1['weight'])
/var/folders/rb/3tb3l22x2tgfhls9_hdg4r6h0000gn/T/ipykernel_85337/2755088573.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a D

Shipment ID      vendor_name fc_code             ship_method  \
0      FBA18WF7Q4K2    Two's Company    ICT2              AMAZON_LTL   
1      FBA18W2KGXCR        R&R Corp.    TMB8  HOUR_LOOP_FEDEX_PARCEL   
2      FBA18VXT1KL7  Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
3      FBA18VSDFCLL          Pet Lou    SCK8  HOUR_LOOP_FEDEX_PARCEL   
4      FBA18VXNQZY7  Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
...             ...              ...     ...                     ...   
51177  FBA15L4PGGQD            Roman    MDW2              AMAZON_LTL   
51178  FBA15L4S2LRV            Roman    MDW2              AMAZON_LTL   
51179  FBA15L4NP43H            Roman    MDW2              AMAZON_LTL   
51180  FBA15L4NP2GJ            Roman    MDW2              AMAZON_LTL   
51181  FBA15L4NZ6V1            Roman    MDW2              AMAZON_LTL   

            date  weight         volume    cost      $/lb  log_cost  \
0     2025-04-27  1102.0  322371.837300  438.18  0.397623  6.084909   
1     2025-04-25   277.0   12838.133560  153.42  0.553863  5.039676   
2     2025-04-25    44.0    1996.951518   30.80  0.700000  3.459466   
3     2025-04-25   489.0  188501.446600  337.96  0.691125  5.825882   
4     2025-04-25   205.0   15855.061380  143.52  0.700098  4.973418   
...          ...     ...            ...     ...       ...       ...   
51177 2005-07-12  2070.0  399124.778300   83.65  0.040411  4.438525   
51178 2005-07-12  1945.0  323510.005300   78.59  0.040406  4.376888   
51179 2005-07-12  1530.0  315711.406000   61.82  0.040405  4.140273   
51180 2005-07-12  1755.0  310488.074300   70.92  0.040410  4.275554   
51181 2005-07-12  1745.0  284252.999000   70.51  0.040407  4.269837   

       log_weight  log_volume  
0        7.005789   12.683464  
1        5.627621    9.460253  
2        3.806662    7.599878  
3        6.194405   12.146866  
4        5.327876    9.671307  
...           ...         ...  
51177    7.635787   12.897032  
51178    7.573531   12.686988  
51179    7.333676   12.662587  
51180    7.470794   12.645904  
51181    7.465083   12.557623  

[51142 rows x 12 columns]

In [111]:
data1 = data1[~data1['ship_method'].isin(['TQL', 'AMAZON_LTL_AWD', 'HOUR_LOOP_UPS_PARCEL', 'OTHER', 'JB_HUNT'])]
data1.loc[data1['ship_method'] == 'WWE', 'ship_method'] = 'WWE_LTL'
conditions = [
    data1['ship_method'].isin(['AMAZON_LTL', 'ESTES', 'UBER_LTL', 'VERTEX', 'WWE_LTL']),
    data1['ship_method'].isin(['AMAZON_FREIGHT', 'UBER_FTL']),
    data1['ship_method'].isin(['AMAZON_UPS_PARCEL', 'HOUR_LOOP_FEDEX_PARCEL', 'WWE_PARCEL'])
]
choices = ['LTL', 'FTL', 'PARCEL']

data1['ship_method_type'] = np.select(conditions, choices, default='other')
data1

Shipment ID      vendor_name fc_code             ship_method  \
0      FBA18WF7Q4K2    Two's Company    ICT2              AMAZON_LTL   
1      FBA18W2KGXCR        R&R Corp.    TMB8  HOUR_LOOP_FEDEX_PARCEL   
2      FBA18VXT1KL7  Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
3      FBA18VSDFCLL          Pet Lou    SCK8  HOUR_LOOP_FEDEX_PARCEL   
4      FBA18VXNQZY7  Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
...             ...              ...     ...                     ...   
51177  FBA15L4PGGQD            Roman    MDW2              AMAZON_LTL   
51178  FBA15L4S2LRV            Roman    MDW2              AMAZON_LTL   
51179  FBA15L4NP43H            Roman    MDW2              AMAZON_LTL   
51180  FBA15L4NP2GJ            Roman    MDW2              AMAZON_LTL   
51181  FBA15L4NZ6V1            Roman    MDW2              AMAZON_LTL   

            date  weight         volume    cost      $/lb  log_cost  \
0     2025-04-27  1102.0  322371.837300  438.18  0.397623  6.084909   
1     2025-04-25   277.0   12838.133560  153.42  0.553863  5.039676   
2     2025-04-25    44.0    1996.951518   30.80  0.700000  3.459466   
3     2025-04-25   489.0  188501.446600  337.96  0.691125  5.825882   
4     2025-04-25   205.0   15855.061380  143.52  0.700098  4.973418   
...          ...     ...            ...     ...       ...       ...   
51177 2005-07-12  2070.0  399124.778300   83.65  0.040411  4.438525   
51178 2005-07-12  1945.0  323510.005300   78.59  0.040406  4.376888   
51179 2005-07-12  1530.0  315711.406000   61.82  0.040405  4.140273   
51180 2005-07-12  1755.0  310488.074300   70.92  0.040410  4.275554   
51181 2005-07-12  1745.0  284252.999000   70.51  0.040407  4.269837   

       log_weight  log_volume ship_method_type  
0        7.005789   12.683464              LTL  
1        5.627621    9.460253           PARCEL  
2        3.806662    7.599878           PARCEL  
3        6.194405   12.146866           PARCEL  
4        5.327876    9.671307           PARCEL  
...           ...         ...              ...  
51177    7.635787   12.897032              LTL  
51178    7.573531   12.686988              LTL  
51179    7.333676   12.662587              LTL  
51180    7.470794   12.645904              LTL  
51181    7.465083   12.557623              LTL  

[50947 rows x 13 columns]

In [112]:
data1['ship_method'].value_counts()

ship_method
AMAZON_UPS_PARCEL         20308
AMAZON_LTL                15799
HOUR_LOOP_FEDEX_PARCEL     8118
AMAZON_FREIGHT             3877
ESTES                      1017
WWE_PARCEL                  524
UBER_LTL                    445
UBER_FTL                    359
VERTEX                      268
WWE_LTL                     232
Name: count, dtype: int64

In [113]:
a = pd.to_datetime('2024-03-01')
b = pd.to_datetime('2025-02-28')

df_pre = data1[data1['date'] < a]
df_train = data1[(data1['date'] >= a) & (data1['date'] <= b)]
df_test = data1[data1['date'] > b]

In [114]:
df_pre.to_csv('Data_v4_before.csv', index = False)
df_train.to_csv('Data_v4_no_geo_and_TVP.csv', index = False)
df_test.to_csv('Data_v4_after.csv', index = False)

In [115]:
data1.info()

<class 'pandas.core.frame.DataFrame'>
Index: 50947 entries, 0 to 51181
Data columns (total 13 columns):
 #   Column            Non-Null Count  Dtype         
---  ------            --------------  -----         
 0   Shipment ID       50947 non-null  object        
 1   vendor_name       50947 non-null  object        
 2   fc_code           50947 non-null  object        
 3   ship_method       50947 non-null  object        
 4   date              50947 non-null  datetime64[ns]
 5   weight            50947 non-null  float64       
 6   volume            50947 non-null  float64       
 7   cost              50947 non-null  float64       
 8   $/lb              50947 non-null  float64       
 9   log_cost          50947 non-null  float64       
 10  log_weight        50947 non-null  float64       
 11  log_volume        50947 non-null  float64       
 12  ship_method_type  50947 non-null  object        
dtypes: datetime64[ns](1), float64(7), object(5)
memory usage: 5.4+ MB


---

### 處理地理資訊

In [67]:
data = data.dropna(subset = ['from_state']) #Original 'NA' means "Not America"
data = data.reset_index(drop = True)
data

Shipment ID          vendor_name fc_code             ship_method  \
0      FBA18WF7Q4K2        Two's Company    ICT2              AMAZON_LTL   
1      FBA18W2KGXCR            R&R Corp.    TMB8  HOUR_LOOP_FEDEX_PARCEL   
2      FBA18VXT1KL7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
3      FBA18VSDFCLL              Pet Lou    SCK8  HOUR_LOOP_FEDEX_PARCEL   
4      FBA18VXNQZY7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
...             ...                  ...     ...                     ...   
32032    FBA5634V16      Grasslands Road    MDW2       AMAZON_UPS_PARCEL   
32033    FBA5219LYK                Donco    MKC4              AMAZON_LTL   
32034    FBA51WQMJ1             Ace Baby    AVP3              AMAZON_LTL   
32035    FBA3VML87B                Roman    MDT1              AMAZON_LTL   
32036  FBA18VQTVBG9  Primitives By Kathy    LBE1              AMAZON_LTL   

            date from_state  from_address_id  total_vendor_price  \
0     2025-04-27         NY             87.0             9941.34   
1     2025-04-25         MD           1858.0             2239.92   
2     2025-04-25         TX          34073.0             1060.32   
3     2025-04-25         CA           6035.0             1685.40   
4     2025-04-25         TX          34073.0             5028.00   
...          ...        ...              ...                 ...   
32032 2017-10-12         WI          20091.0                 NaN   
32033 2017-08-25         TX          14155.0                 NaN   
32034 2017-08-18         CA           7264.0                 NaN   
32035 2016-09-01         IL           7950.0                 NaN   
32036 2069-12-31         NJ          37174.0             1404.00   

      from_postal_code  amount  weight      $/lb esti_dimensional_volume  
0                10523  438.18  1102.0  0.397623             322371.8373  
1                20852  153.42   277.0  0.553863             12838.13356  
2                75033   30.80    44.0  0.700000             1996.951518  
3                91761  337.96   489.0  0.691125             188501.4466  
4                75033  143.52   205.0  0.700098             15855.06138  
...                ...     ...     ...       ...                     ...  
32032            54437  118.75   411.0  0.288929              41523.8022  
32033            76140  802.35  9632.0  0.083300                   #NUM!  
32034            91331  211.71   690.0  0.306826                18026.25  
32035            60108  156.47   614.0  0.254837             134147.7806  
32036             8817  126.52   180.0  0.702889             27798.95621  

[32037 rows x 13 columns]

In [68]:
#處理地理資訊
nomi = pg.Nominatim('us')
geo_info = nomi.query_postal_code(data['from_postal_code'].tolist())

data['latitude'] = geo_info['latitude'] #緯度
data['longitude'] = geo_info['longitude'] #經度
data['from_city'] = geo_info['place_name']  #城市or地區
#data['from_state'] = geo_info['state_code']  #處理 from_state NA 的異常值

data

Shipment ID          vendor_name fc_code             ship_method  \
0      FBA18WF7Q4K2        Two's Company    ICT2              AMAZON_LTL   
1      FBA18W2KGXCR            R&R Corp.    TMB8  HOUR_LOOP_FEDEX_PARCEL   
2      FBA18VXT1KL7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
3      FBA18VSDFCLL              Pet Lou    SCK8  HOUR_LOOP_FEDEX_PARCEL   
4      FBA18VXNQZY7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
...             ...                  ...     ...                     ...   
32032    FBA5634V16      Grasslands Road    MDW2       AMAZON_UPS_PARCEL   
32033    FBA5219LYK                Donco    MKC4              AMAZON_LTL   
32034    FBA51WQMJ1             Ace Baby    AVP3              AMAZON_LTL   
32035    FBA3VML87B                Roman    MDT1              AMAZON_LTL   
32036  FBA18VQTVBG9  Primitives By Kathy    LBE1              AMAZON_LTL   

            date from_state  from_address_id  total_vendor_price  \
0     2025-04-27         NY             87.0             9941.34   
1     2025-04-25         MD           1858.0             2239.92   
2     2025-04-25         TX          34073.0             1060.32   
3     2025-04-25         CA           6035.0             1685.40   
4     2025-04-25         TX          34073.0             5028.00   
...          ...        ...              ...                 ...   
32032 2017-10-12         WI          20091.0                 NaN   
32033 2017-08-25         TX          14155.0                 NaN   
32034 2017-08-18         CA           7264.0                 NaN   
32035 2016-09-01         IL           7950.0                 NaN   
32036 2069-12-31         NJ          37174.0             1404.00   

      from_postal_code  amount  weight      $/lb esti_dimensional_volume  \
0                10523  438.18  1102.0  0.397623             322371.8373   
1                20852  153.42   277.0  0.553863             12838.13356   
2                75033   30.80    44.0  0.700000             1996.951518   
3                91761  337.96   489.0  0.691125             188501.4466   
4                75033  143.52   205.0  0.700098             15855.06138   
...                ...     ...     ...       ...                     ...   
32032            54437  118.75   411.0  0.288929              41523.8022   
32033            76140  802.35  9632.0  0.083300                   #NUM!   
32034            91331  211.71   690.0  0.306826                18026.25   
32035            60108  156.47   614.0  0.254837             134147.7806   
32036             8817  126.52   180.0  0.702889             27798.95621   

       latitude  longitude     from_city  
0       41.0572   -73.8136      Elmsford  
1       39.0496   -77.1204     Rockville  
2       33.2559   -96.8853        Frisco  
3       34.0316  -117.6187       Ontario  
4       33.2559   -96.8853        Frisco  
...         ...        ...           ...  
32032   44.7404   -90.6229     Greenwood  
32033   32.6192   -97.2735    Fort Worth  
32034   34.2556  -118.4208       Pacoima  
32035   41.9483   -88.0782  Bloomingdale  
32036       NaN        NaN           NaN  

[32037 rows x 16 columns]

In [69]:
#地理資訊處理格式錯誤問題(zip-9, zip-4)
zip9 = []
zip4 = []
weird = []
no_geo = data['latitude'].isna()
for i in range(len(data)):
    if no_geo.iloc[i] == True:
        if len(data['from_postal_code'].iloc[i]) == 10:
            zip9.append(i)
        elif len(data['from_postal_code'].iloc[i]) == 4:
            zip4.append(i)
        else:
            weird.append(i)

for i in zip9:
    zip5 = data['from_postal_code'].iloc[i][:5]
    geo_info = nomi.query_postal_code(zip5)
    data['latitude'].iloc[i] = geo_info['latitude'] #緯度
    data['longitude'].iloc[i] = geo_info['longitude'] #經度
    data['from_city'].iloc[i] = geo_info['place_name']  #城市or地區

for i in zip4:
    zip4 = '0' + data['from_postal_code'].iloc[i]
    geo_info = nomi.query_postal_code(zip4)
    data['latitude'].iloc[i] = geo_info['latitude'] #緯度
    data['longitude'].iloc[i] = geo_info['longitude'] #經度
    data['from_city'].iloc[i] = geo_info['place_name']  #城市or地區

data

/var/folders/rb/3tb3l22x2tgfhls9_hdg4r6h0000gn/T/ipykernel_85337/2828640717.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['latitude'].iloc[i] = geo_info['latitude'] #緯度
/var/folders/rb/3tb3l22x2tgfhls9_hdg4r6h0000gn/T/ipykernel_85337/2828640717.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['longitude'].iloc[i] = geo_info['longitude'] #經度
/var/folders/rb/3tb3l22x2tgfhls9_hdg4r6h0000gn/T/ipykernel_85337/2828640717.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user

Shipment ID          vendor_name fc_code             ship_method  \
0      FBA18WF7Q4K2        Two's Company    ICT2              AMAZON_LTL   
1      FBA18W2KGXCR            R&R Corp.    TMB8  HOUR_LOOP_FEDEX_PARCEL   
2      FBA18VXT1KL7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
3      FBA18VSDFCLL              Pet Lou    SCK8  HOUR_LOOP_FEDEX_PARCEL   
4      FBA18VXNQZY7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
...             ...                  ...     ...                     ...   
32032    FBA5634V16      Grasslands Road    MDW2       AMAZON_UPS_PARCEL   
32033    FBA5219LYK                Donco    MKC4              AMAZON_LTL   
32034    FBA51WQMJ1             Ace Baby    AVP3              AMAZON_LTL   
32035    FBA3VML87B                Roman    MDT1              AMAZON_LTL   
32036  FBA18VQTVBG9  Primitives By Kathy    LBE1              AMAZON_LTL   

            date from_state  from_address_id  total_vendor_price  \
0     2025-04-27         NY             87.0             9941.34   
1     2025-04-25         MD           1858.0             2239.92   
2     2025-04-25         TX          34073.0             1060.32   
3     2025-04-25         CA           6035.0             1685.40   
4     2025-04-25         TX          34073.0             5028.00   
...          ...        ...              ...                 ...   
32032 2017-10-12         WI          20091.0                 NaN   
32033 2017-08-25         TX          14155.0                 NaN   
32034 2017-08-18         CA           7264.0                 NaN   
32035 2016-09-01         IL           7950.0                 NaN   
32036 2069-12-31         NJ          37174.0             1404.00   

      from_postal_code  amount  weight      $/lb esti_dimensional_volume  \
0                10523  438.18  1102.0  0.397623             322371.8373   
1                20852  153.42   277.0  0.553863             12838.13356   
2                75033   30.80    44.0  0.700000             1996.951518   
3                91761  337.96   489.0  0.691125             188501.4466   
4                75033  143.52   205.0  0.700098             15855.06138   
...                ...     ...     ...       ...                     ...   
32032            54437  118.75   411.0  0.288929              41523.8022   
32033            76140  802.35  9632.0  0.083300                   #NUM!   
32034            91331  211.71   690.0  0.306826                18026.25   
32035            60108  156.47   614.0  0.254837             134147.7806   
32036             8817  126.52   180.0  0.702889             27798.95621   

       latitude  longitude     from_city  
0       41.0572   -73.8136      Elmsford  
1       39.0496   -77.1204     Rockville  
2       33.2559   -96.8853        Frisco  
3       34.0316  -117.6187       Ontario  
4       33.2559   -96.8853        Frisco  
...         ...        ...           ...  
32032   44.7404   -90.6229     Greenwood  
32033   32.6192   -97.2735    Fort Worth  
32034   34.2556  -118.4208       Pacoima  
32035   41.9483   -88.0782  Bloomingdale  
32036   40.5171   -74.3973        Edison  

[32037 rows x 16 columns]

In [70]:
#處理加拿大的地理資訊
nomi = pg.Nominatim('ca')

for i in weird:
    geo_info = nomi.query_postal_code(data['from_postal_code'].iloc[i])
    data['latitude'].iloc[i] = geo_info['latitude'] #緯度
    data['longitude'].iloc[i] = geo_info['longitude'] #經度
    data['from_city'].iloc[i] = geo_info['place_name']  #城市or地區

data

/var/folders/rb/3tb3l22x2tgfhls9_hdg4r6h0000gn/T/ipykernel_85337/588957492.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['latitude'].iloc[i] = geo_info['latitude'] #緯度
/var/folders/rb/3tb3l22x2tgfhls9_hdg4r6h0000gn/T/ipykernel_85337/588957492.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['longitude'].iloc[i] = geo_info['longitude'] #經度
/var/folders/rb/3tb3l22x2tgfhls9_hdg4r6h0000gn/T/ipykernel_85337/588957492.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide

Shipment ID          vendor_name fc_code             ship_method  \
0      FBA18WF7Q4K2        Two's Company    ICT2              AMAZON_LTL   
1      FBA18W2KGXCR            R&R Corp.    TMB8  HOUR_LOOP_FEDEX_PARCEL   
2      FBA18VXT1KL7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
3      FBA18VSDFCLL              Pet Lou    SCK8  HOUR_LOOP_FEDEX_PARCEL   
4      FBA18VXNQZY7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
...             ...                  ...     ...                     ...   
32032    FBA5634V16      Grasslands Road    MDW2       AMAZON_UPS_PARCEL   
32033    FBA5219LYK                Donco    MKC4              AMAZON_LTL   
32034    FBA51WQMJ1             Ace Baby    AVP3              AMAZON_LTL   
32035    FBA3VML87B                Roman    MDT1              AMAZON_LTL   
32036  FBA18VQTVBG9  Primitives By Kathy    LBE1              AMAZON_LTL   

            date from_state  from_address_id  total_vendor_price  \
0     2025-04-27         NY             87.0             9941.34   
1     2025-04-25         MD           1858.0             2239.92   
2     2025-04-25         TX          34073.0             1060.32   
3     2025-04-25         CA           6035.0             1685.40   
4     2025-04-25         TX          34073.0             5028.00   
...          ...        ...              ...                 ...   
32032 2017-10-12         WI          20091.0                 NaN   
32033 2017-08-25         TX          14155.0                 NaN   
32034 2017-08-18         CA           7264.0                 NaN   
32035 2016-09-01         IL           7950.0                 NaN   
32036 2069-12-31         NJ          37174.0             1404.00   

      from_postal_code  amount  weight      $/lb esti_dimensional_volume  \
0                10523  438.18  1102.0  0.397623             322371.8373   
1                20852  153.42   277.0  0.553863             12838.13356   
2                75033   30.80    44.0  0.700000             1996.951518   
3                91761  337.96   489.0  0.691125             188501.4466   
4                75033  143.52   205.0  0.700098             15855.06138   
...                ...     ...     ...       ...                     ...   
32032            54437  118.75   411.0  0.288929              41523.8022   
32033            76140  802.35  9632.0  0.083300                   #NUM!   
32034            91331  211.71   690.0  0.306826                18026.25   
32035            60108  156.47   614.0  0.254837             134147.7806   
32036             8817  126.52   180.0  0.702889             27798.95621   

       latitude  longitude     from_city  
0       41.0572   -73.8136      Elmsford  
1       39.0496   -77.1204     Rockville  
2       33.2559   -96.8853        Frisco  
3       34.0316  -117.6187       Ontario  
4       33.2559   -96.8853        Frisco  
...         ...        ...           ...  
32032   44.7404   -90.6229     Greenwood  
32033   32.6192   -97.2735    Fort Worth  
32034   34.2556  -118.4208       Pacoima  
32035   41.9483   -88.0782  Bloomingdale  
32036   40.5171   -74.3973        Edison  

[32037 rows x 16 columns]

In [71]:
data[data['longitude'].isna()]

Shipment ID             vendor_name fc_code             ship_method  \
15393  FBA17PXR739D                   Roman    MDW2              AMAZON_LTL   
15425  FBA17PXR736T                   Roman    CMH3              AMAZON_LTL   
15747  FBA17PQW51SF               Next Glow    TEB9              AMAZON_LTL   
16496  FBA177Y0PY52    Your Heart's Delight    TEB9  HOUR_LOOP_FEDEX_PARCEL   
16790  FBA17JHBVZ6B            Bella & Bear    LAX9              AMAZON_LTL   
17525  FBA17HCH4NCW            Bella & Bear    SBD1              AMAZON_LTL   
21795  FBA177Y0PY52    Your Heart's Delight    TEB9  HOUR_LOOP_FEDEX_PARCEL   
24594  FBA16ZL3GM3K  Claude Lakey Woodwinds    SMF3  HOUR_LOOP_FEDEX_PARCEL   
27225  FBA16ZL3GM3K  Claude Lakey Woodwinds    SMF3  HOUR_LOOP_FEDEX_PARCEL   
27388  FBA16ZJX289C               Baby Jack    MDW2       AMAZON_UPS_PARCEL   
27527  FBA16XQVMDW0  Claude Lakey Woodwinds    SBD1  HOUR_LOOP_FEDEX_PARCEL   
30969  FBA16L1VRGHW        Rio Grande Games    IND9              AMAZON_LTL   

            date from_state  from_address_id  total_vendor_price  \
15393 2024-02-21         IL          20228.0            41254.75   
15425 2024-02-19         IL          20228.0             8095.50   
15747 2024-02-06         NJ          20415.0             2543.00   
16496 2023-12-30         NJ          14723.0             2154.00   
16790 2023-11-30         CA           6877.0             2484.00   
17525 2023-11-07         CA           6877.0             4975.44   
21795 2023-07-31         NJ          14723.0             2154.00   
24594 2023-04-30         WA           3349.0                 NaN   
27225 2022-12-31         WA           3349.0                 NaN   
27388 2022-12-14         WI           1853.0                 NaN   
27527 2022-11-30         WA           3349.0                 NaN   
30969 2022-02-20         IN            811.0                 NaN   

        from_postal_code  amount  weight       $/lb esti_dimensional_volume  \
15393  601080L-Y9D1-S8WC  410.36  5531.0   0.074193             665085.3079   
15425  601080L-Y9D1-S8WC  482.13  1250.0   0.385704             427927.7268   
15747               7250  137.53   200.0   0.687650             42823.26113   
16496              80322  143.31   111.0   1.291081              52780.5462   
16790             92064   117.69   351.0   0.335299             13746.21763   
17525             92064   140.00   867.0   0.161476             24447.02227   
21795              80322  156.44   413.0   0.378789              52780.5462   
24594              98210   30.33     2.0  15.165000               88.955179   
27225              98210   28.32     2.0  14.160000               88.955179   
27388             53149     7.33    24.0   0.305417              13446.5697   
27527              98210   14.22     3.0   4.740000              173.140976   
30969        46798-17815   98.66   320.0   0.308312             29494.08738   

       latitude  longitude from_city  
15393       NaN        NaN       NaN  
15425       NaN        NaN       NaN  
15747       NaN        NaN       NaN  
16496       NaN        NaN       NaN  
16790       NaN        NaN       NaN  
17525       NaN        NaN       NaN  
21795       NaN        NaN       NaN  
24594       NaN        NaN       NaN  
27225       NaN        NaN       NaN  
27388       NaN        NaN       NaN  
27527       NaN        NaN       NaN  
30969       NaN        NaN       NaN

In [75]:
data = data.dropna(subset=['latitude'])
data = data.reset_index(drop=True)
data

Shipment ID          vendor_name fc_code             ship_method  \
0      FBA18WF7Q4K2        Two's Company    ICT2              AMAZON_LTL   
1      FBA18W2KGXCR            R&R Corp.    TMB8  HOUR_LOOP_FEDEX_PARCEL   
2      FBA18VXT1KL7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
3      FBA18VSDFCLL              Pet Lou    SCK8  HOUR_LOOP_FEDEX_PARCEL   
4      FBA18VXNQZY7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
...             ...                  ...     ...                     ...   
32020    FBA5634V16      Grasslands Road    MDW2       AMAZON_UPS_PARCEL   
32021    FBA5219LYK                Donco    MKC4              AMAZON_LTL   
32022    FBA51WQMJ1             Ace Baby    AVP3              AMAZON_LTL   
32023    FBA3VML87B                Roman    MDT1              AMAZON_LTL   
32024  FBA18VQTVBG9  Primitives By Kathy    LBE1              AMAZON_LTL   

            date from_state  from_address_id  total_vendor_price  \
0     2025-04-27         NY             87.0             9941.34   
1     2025-04-25         MD           1858.0             2239.92   
2     2025-04-25         TX          34073.0             1060.32   
3     2025-04-25         CA           6035.0             1685.40   
4     2025-04-25         TX          34073.0             5028.00   
...          ...        ...              ...                 ...   
32020 2017-10-12         WI          20091.0                 NaN   
32021 2017-08-25         TX          14155.0                 NaN   
32022 2017-08-18         CA           7264.0                 NaN   
32023 2016-09-01         IL           7950.0                 NaN   
32024 2069-12-31         NJ          37174.0             1404.00   

      from_postal_code  amount  weight      $/lb esti_dimensional_volume  \
0                10523  438.18  1102.0  0.397623             322371.8373   
1                20852  153.42   277.0  0.553863             12838.13356   
2                75033   30.80    44.0  0.700000             1996.951518   
3                91761  337.96   489.0  0.691125             188501.4466   
4                75033  143.52   205.0  0.700098             15855.06138   
...                ...     ...     ...       ...                     ...   
32020            54437  118.75   411.0  0.288929              41523.8022   
32021            76140  802.35  9632.0  0.083300                   #NUM!   
32022            91331  211.71   690.0  0.306826                18026.25   
32023            60108  156.47   614.0  0.254837             134147.7806   
32024             8817  126.52   180.0  0.702889             27798.95621   

       latitude  longitude     from_city  
0       41.0572   -73.8136      Elmsford  
1       39.0496   -77.1204     Rockville  
2       33.2559   -96.8853        Frisco  
3       34.0316  -117.6187       Ontario  
4       33.2559   -96.8853        Frisco  
...         ...        ...           ...  
32020   44.7404   -90.6229     Greenwood  
32021   32.6192   -97.2735    Fort Worth  
32022   34.2556  -118.4208       Pacoima  
32023   41.9483   -88.0782  Bloomingdale  
32024   40.5171   -74.3973        Edison  

[32025 rows x 16 columns]

In [76]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 32025 entries, 0 to 32024
Data columns (total 16 columns):
 #   Column                   Non-Null Count  Dtype         
---  ------                   --------------  -----         
 0   Shipment ID              32025 non-null  object        
 1   vendor_name              32025 non-null  object        
 2   fc_code                  32025 non-null  object        
 3   ship_method              32025 non-null  object        
 4   date                     32025 non-null  datetime64[ns]
 5   from_state               32025 non-null  object        
 6   from_address_id          32025 non-null  float64       
 7   total_vendor_price       23638 non-null  float64       
 8   from_postal_code         32025 non-null  object        
 9   amount                   32025 non-null  float64       
 10  weight                   32025 non-null  float64       
 11  $/lb                     32025 non-null  float64       
 12  esti_dimensional_volume  32025 n

In [77]:
del data['from_address_id']

In [78]:
data_with_no_fc = data
data_with_no_fc

Shipment ID          vendor_name fc_code             ship_method  \
0      FBA18WF7Q4K2        Two's Company    ICT2              AMAZON_LTL   
1      FBA18W2KGXCR            R&R Corp.    TMB8  HOUR_LOOP_FEDEX_PARCEL   
2      FBA18VXT1KL7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
3      FBA18VSDFCLL              Pet Lou    SCK8  HOUR_LOOP_FEDEX_PARCEL   
4      FBA18VXNQZY7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
...             ...                  ...     ...                     ...   
32020    FBA5634V16      Grasslands Road    MDW2       AMAZON_UPS_PARCEL   
32021    FBA5219LYK                Donco    MKC4              AMAZON_LTL   
32022    FBA51WQMJ1             Ace Baby    AVP3              AMAZON_LTL   
32023    FBA3VML87B                Roman    MDT1              AMAZON_LTL   
32024  FBA18VQTVBG9  Primitives By Kathy    LBE1              AMAZON_LTL   

            date from_state  total_vendor_price from_postal_code  amount  \
0     2025-04-27         NY             9941.34            10523  438.18   
1     2025-04-25         MD             2239.92            20852  153.42   
2     2025-04-25         TX             1060.32            75033   30.80   
3     2025-04-25         CA             1685.40            91761  337.96   
4     2025-04-25         TX             5028.00            75033  143.52   
...          ...        ...                 ...              ...     ...   
32020 2017-10-12         WI                 NaN            54437  118.75   
32021 2017-08-25         TX                 NaN            76140  802.35   
32022 2017-08-18         CA                 NaN            91331  211.71   
32023 2016-09-01         IL                 NaN            60108  156.47   
32024 2069-12-31         NJ             1404.00             8817  126.52   

       weight      $/lb esti_dimensional_volume  latitude  longitude  \
0      1102.0  0.397623             322371.8373   41.0572   -73.8136   
1       277.0  0.553863             12838.13356   39.0496   -77.1204   
2        44.0  0.700000             1996.951518   33.2559   -96.8853   
3       489.0  0.691125             188501.4466   34.0316  -117.6187   
4       205.0  0.700098             15855.06138   33.2559   -96.8853   
...       ...       ...                     ...       ...        ...   
32020   411.0  0.288929              41523.8022   44.7404   -90.6229   
32021  9632.0  0.083300                   #NUM!   32.6192   -97.2735   
32022   690.0  0.306826                18026.25   34.2556  -118.4208   
32023   614.0  0.254837             134147.7806   41.9483   -88.0782   
32024   180.0  0.702889             27798.95621   40.5171   -74.3973   

          from_city  
0          Elmsford  
1         Rockville  
2            Frisco  
3           Ontario  
4            Frisco  
...             ...  
32020     Greenwood  
32021    Fort Worth  
32022       Pacoima  
32023  Bloomingdale  
32024        Edison  

[32025 rows x 15 columns]

## 處理 Amazon FC 位置資訊並合併兩檔案

In [93]:
data = data_with_no_fc

In [94]:
fc = pd.read_csv('fc.csv')
fc

Unnamed: 0 FC_code  Days to Ship                           Line1  \
0             0    ABE2             3               705 Boulder Drive   
1             1    ABE3             3               650 Boulder Drive   
2             2    ABE4             3             1610 Van Buren Road   
3             3    ABE8             3           401 Independence Road   
4             4    ABQ2             3             6251 Pioneer Trl NW   
..          ...     ...           ...                             ...   
258         258    XLX1             3                 1115 Wesel Blvd   
259         259    XLX3             3     21590 Needham Ranch Parkway   
260         260    XLX6             7  12220 Carolina Logistics Drive   
261         261    XLX7             7                18580 GATEWAY DR   
262         262    XRI3             7                4949 Commerce Rd   

              City State Postal Code  \
0    Breinigsville    PA  18031-1533   
1    Breinigsville    PA  18031-1536   
2           Easton    PA  18045-7807   
3         Florence    NJ  08518-2200   
4        Los Lunas    NM       87031   
..             ...   ...         ...   
258     Hagerstown    MD  21740-8126   
259  Santa Clarita    CA       91321   
260      Pineville    NC       28134   
261    Victorville    CA       92394   
262       Richmond    VA       23234   

                                   full_address   latitude   longitude  
0            705 Boulder Drive, 18031-1533, USA  40.559630  -75.620286  
1            650 Boulder Drive, 18031-1536, USA  40.560787  -75.621052  
2          1610 Van Buren Road, 18045-7807, USA  40.442490  -74.464292  
3        401 Independence Road, 08518-2200, USA  40.110056  -74.802525  
4               6251 Pioneer Trl NW, 87031, USA  34.825543 -106.815218  
..                                          ...        ...         ...  
258            1115 Wesel Blvd, 21740-8126, USA  39.636964  -77.746751  
259     21590 Needham Ranch Parkway, 91321, USA  34.367747 -118.517772  
260  12220 Carolina Logistics Drive, 28134, USA  35.102603  -80.914335  
261                18580 GATEWAY DR, 92394, USA  34.498671 -117.375064  
262                4949 Commerce Rd, 23234, USA  34.111259  -83.336277  

[263 rows x 10 columns]

In [95]:
fc.rename(columns = {
    'FC_code' : 'fc_code',
    'City' : 'to_city',
    'State' : 'to_state',
    'Postal Code' : 'to_postal_code',
    'full_address' : 'to_full_address',
    'latitude' : 'to_latitude',
    'longitude' : 'to_longitude'
}, inplace = True)

del fc['Line1']
del fc['Unnamed: 0']
del fc['to_full_address']

fc

fc_code  Days to Ship        to_city to_state to_postal_code  to_latitude  \
0      ABE2             3  Breinigsville       PA     18031-1533    40.559630   
1      ABE3             3  Breinigsville       PA     18031-1536    40.560787   
2      ABE4             3         Easton       PA     18045-7807    40.442490   
3      ABE8             3       Florence       NJ     08518-2200    40.110056   
4      ABQ2             3      Los Lunas       NM          87031    34.825543   
..      ...           ...            ...      ...            ...          ...   
258    XLX1             3     Hagerstown       MD     21740-8126    39.636964   
259    XLX3             3  Santa Clarita       CA          91321    34.367747   
260    XLX6             7      Pineville       NC          28134    35.102603   
261    XLX7             7    Victorville       CA          92394    34.498671   
262    XRI3             7       Richmond       VA          23234    34.111259   

     to_longitude  
0      -75.620286  
1      -75.621052  
2      -74.464292  
3      -74.802525  
4     -106.815218  
..            ...  
258    -77.746751  
259   -118.517772  
260    -80.914335  
261   -117.375064  
262    -83.336277  

[263 rows x 7 columns]

In [96]:
data.rename(columns = {
    'amount' : 'cost',
    'latitude' : 'from_latitude',
    'longitude' : 'from_longitude',
    'esti_dimensional_volume' : 'volume'
}, inplace = True)

data

Shipment ID          vendor_name fc_code             ship_method  \
0      FBA18WF7Q4K2        Two's Company    ICT2              AMAZON_LTL   
1      FBA18W2KGXCR            R&R Corp.    TMB8  HOUR_LOOP_FEDEX_PARCEL   
2      FBA18VXT1KL7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
3      FBA18VSDFCLL              Pet Lou    SCK8  HOUR_LOOP_FEDEX_PARCEL   
4      FBA18VXNQZY7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
...             ...                  ...     ...                     ...   
32020    FBA5634V16      Grasslands Road    MDW2       AMAZON_UPS_PARCEL   
32021    FBA5219LYK                Donco    MKC4              AMAZON_LTL   
32022    FBA51WQMJ1             Ace Baby    AVP3              AMAZON_LTL   
32023    FBA3VML87B                Roman    MDT1              AMAZON_LTL   
32024  FBA18VQTVBG9  Primitives By Kathy    LBE1              AMAZON_LTL   

            date from_state  total_vendor_price from_postal_code    cost  \
0     2025-04-27         NY             9941.34            10523  438.18   
1     2025-04-25         MD             2239.92            20852  153.42   
2     2025-04-25         TX             1060.32            75033   30.80   
3     2025-04-25         CA             1685.40            91761  337.96   
4     2025-04-25         TX             5028.00            75033  143.52   
...          ...        ...                 ...              ...     ...   
32020 2017-10-12         WI                 NaN            54437  118.75   
32021 2017-08-25         TX                 NaN            76140  802.35   
32022 2017-08-18         CA                 NaN            91331  211.71   
32023 2016-09-01         IL                 NaN            60108  156.47   
32024 2069-12-31         NJ             1404.00             8817  126.52   

       weight      $/lb       volume  from_latitude  from_longitude  \
0      1102.0  0.397623  322371.8373        41.0572        -73.8136   
1       277.0  0.553863  12838.13356        39.0496        -77.1204   
2        44.0  0.700000  1996.951518        33.2559        -96.8853   
3       489.0  0.691125  188501.4466        34.0316       -117.6187   
4       205.0  0.700098  15855.06138        33.2559        -96.8853   
...       ...       ...          ...            ...             ...   
32020   411.0  0.288929   41523.8022        44.7404        -90.6229   
32021  9632.0  0.083300        #NUM!        32.6192        -97.2735   
32022   690.0  0.306826     18026.25        34.2556       -118.4208   
32023   614.0  0.254837  134147.7806        41.9483        -88.0782   
32024   180.0  0.702889  27798.95621        40.5171        -74.3973   

          from_city  
0          Elmsford  
1         Rockville  
2            Frisco  
3           Ontario  
4            Frisco  
...             ...  
32020     Greenwood  
32021    Fort Worth  
32022       Pacoima  
32023  Bloomingdale  
32024        Edison  

[32025 rows x 15 columns]

In [97]:
#合併兩資料
merged = pd.merge(data, fc, on = 'fc_code', how = 'left')
merged

Shipment ID          vendor_name fc_code             ship_method  \
0      FBA18WF7Q4K2        Two's Company    ICT2              AMAZON_LTL   
1      FBA18W2KGXCR            R&R Corp.    TMB8  HOUR_LOOP_FEDEX_PARCEL   
2      FBA18VXT1KL7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
3      FBA18VSDFCLL              Pet Lou    SCK8  HOUR_LOOP_FEDEX_PARCEL   
4      FBA18VXNQZY7      Glimmer Goddess    TMB8  HOUR_LOOP_FEDEX_PARCEL   
...             ...                  ...     ...                     ...   
32020    FBA5634V16      Grasslands Road    MDW2       AMAZON_UPS_PARCEL   
32021    FBA5219LYK                Donco    MKC4              AMAZON_LTL   
32022    FBA51WQMJ1             Ace Baby    AVP3              AMAZON_LTL   
32023    FBA3VML87B                Roman    MDT1              AMAZON_LTL   
32024  FBA18VQTVBG9  Primitives By Kathy    LBE1              AMAZON_LTL   

            date from_state  total_vendor_price from_postal_code    cost  \
0     2025-04-27         NY             9941.34            10523  438.18   
1     2025-04-25         MD             2239.92            20852  153.42   
2     2025-04-25         TX             1060.32            75033   30.80   
3     2025-04-25         CA             1685.40            91761  337.96   
4     2025-04-25         TX             5028.00            75033  143.52   
...          ...        ...                 ...              ...     ...   
32020 2017-10-12         WI                 NaN            54437  118.75   
32021 2017-08-25         TX                 NaN            76140  802.35   
32022 2017-08-18         CA                 NaN            91331  211.71   
32023 2016-09-01         IL                 NaN            60108  156.47   
32024 2069-12-31         NJ             1404.00             8817  126.52   

       weight  ...       volume from_latitude  from_longitude     from_city  \
0      1102.0  ...  322371.8373       41.0572        -73.8136      Elmsford   
1       277.0  ...  12838.13356       39.0496        -77.1204     Rockville   
2        44.0  ...  1996.951518       33.2559        -96.8853        Frisco   
3       489.0  ...  188501.4466       34.0316       -117.6187       Ontario   
4       205.0  ...  15855.06138       33.2559        -96.8853        Frisco   
...       ...  ...          ...           ...             ...           ...   
32020   411.0  ...   41523.8022       44.7404        -90.6229     Greenwood   
32021  9632.0  ...        #NUM!       32.6192        -97.2735    Fort Worth   
32022   690.0  ...     18026.25       34.2556       -118.4208       Pacoima   
32023   614.0  ...  134147.7806       41.9483        -88.0782  Bloomingdale   
32024   180.0  ...  27798.95621       40.5171        -74.3973        Edison   

      Days to Ship      to_city to_state to_postal_code to_latitude  \
0                3    Park City       KS     67219-1410   39.223754   
1                7    Homestead       FL          33032   25.523886   
2                7    Homestead       FL          33032   25.523886   
3                3       Oakley       CA     94561-2677   38.012304   
4                7    Homestead       FL          33032   25.523886   
...            ...          ...      ...            ...         ...   
32020            3       Joliet       IL     60433-3280   42.027269   
32021            3     Edgerton       KS     66021-9588   38.772815   
32022            3   Gouldsboro       PA     18424-9492   40.733316   
32023            3     Carlisle       PA     17015-7871   42.082922   
32024            7  New Stanton       PA          15672   40.233283   

       to_longitude  
0        -94.585482  
1        -80.404454  
2        -80.404454  
3       -121.747047  
4        -80.404454  
...             ...  
32020    -88.199607  
32021    -94.945809  
32022    -73.980756  
32023    -71.113293  
32024    -79.627933  

[32025 rows x 21 columns]

In [98]:
merged.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 32025 entries, 0 to 32024
Data columns (total 21 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   Shipment ID         32025 non-null  object        
 1   vendor_name         32025 non-null  object        
 2   fc_code             32025 non-null  object        
 3   ship_method         32025 non-null  object        
 4   date                32025 non-null  datetime64[ns]
 5   from_state          32025 non-null  object        
 6   total_vendor_price  23638 non-null  float64       
 7   from_postal_code    32025 non-null  object        
 8   cost                32025 non-null  float64       
 9   weight              32025 non-null  float64       
 10  $/lb                32025 non-null  float64       
 11  volume              32025 non-null  object        
 12  from_latitude       32025 non-null  float64       
 13  from_longitude      32025 non-null  float64   

In [100]:
merged = merged[['Shipment ID', 'ship_method', 'vendor_name', 'date', 'fc_code', 'Days to Ship',
                 'from_postal_code', 'from_state', 'from_city', 'from_latitude', 'from_longitude',
                 'to_postal_code', 'to_state', 'to_city', 'to_latitude', 'to_longitude',
                 'total_vendor_price', 'weight', 'volume', 'cost', '$/lb']]

merged

Shipment ID             ship_method          vendor_name       date  \
0      FBA18WF7Q4K2              AMAZON_LTL        Two's Company 2025-04-27   
1      FBA18W2KGXCR  HOUR_LOOP_FEDEX_PARCEL            R&R Corp. 2025-04-25   
2      FBA18VXT1KL7  HOUR_LOOP_FEDEX_PARCEL      Glimmer Goddess 2025-04-25   
3      FBA18VSDFCLL  HOUR_LOOP_FEDEX_PARCEL              Pet Lou 2025-04-25   
4      FBA18VXNQZY7  HOUR_LOOP_FEDEX_PARCEL      Glimmer Goddess 2025-04-25   
...             ...                     ...                  ...        ...   
32020    FBA5634V16       AMAZON_UPS_PARCEL      Grasslands Road 2017-10-12   
32021    FBA5219LYK              AMAZON_LTL                Donco 2017-08-25   
32022    FBA51WQMJ1              AMAZON_LTL             Ace Baby 2017-08-18   
32023    FBA3VML87B              AMAZON_LTL                Roman 2016-09-01   
32024  FBA18VQTVBG9              AMAZON_LTL  Primitives By Kathy 2069-12-31   

      fc_code  Days to Ship from_postal_code from_state     from_city  \
0        ICT2             3            10523         NY      Elmsford   
1        TMB8             7            20852         MD     Rockville   
2        TMB8             7            75033         TX        Frisco   
3        SCK8             3            91761         CA       Ontario   
4        TMB8             7            75033         TX        Frisco   
...       ...           ...              ...        ...           ...   
32020    MDW2             3            54437         WI     Greenwood   
32021    MKC4             3            76140         TX    Fort Worth   
32022    AVP3             3            91331         CA       Pacoima   
32023    MDT1             3            60108         IL  Bloomingdale   
32024    LBE1             7             8817         NJ        Edison   

       from_latitude  ...  to_postal_code to_state      to_city to_latitude  \
0            41.0572  ...      67219-1410       KS    Park City   39.223754   
1            39.0496  ...           33032       FL    Homestead   25.523886   
2            33.2559  ...           33032       FL    Homestead   25.523886   
3            34.0316  ...      94561-2677       CA       Oakley   38.012304   
4            33.2559  ...           33032       FL    Homestead   25.523886   
...              ...  ...             ...      ...          ...         ...   
32020        44.7404  ...      60433-3280       IL       Joliet   42.027269   
32021        32.6192  ...      66021-9588       KS     Edgerton   38.772815   
32022        34.2556  ...      18424-9492       PA   Gouldsboro   40.733316   
32023        41.9483  ...      17015-7871       PA     Carlisle   42.082922   
32024        40.5171  ...           15672       PA  New Stanton   40.233283   

       to_longitude  total_vendor_price  weight       volume    cost      $/lb  
0        -94.585482             9941.34  1102.0  322371.8373  438.18  0.397623  
1        -80.404454             2239.92   277.0  12838.13356  153.42  0.553863  
2        -80.404454             1060.32    44.0  1996.951518   30.80  0.700000  
3       -121.747047             1685.40   489.0  188501.4466  337.96  0.691125  
4        -80.404454             5028.00   205.0  15855.06138  143.52  0.700098  
...             ...                 ...     ...          ...     ...       ...  
32020    -88.199607                 NaN   411.0   41523.8022  118.75  0.288929  
32021    -94.945809                 NaN  9632.0        #NUM!  802.35  0.083300  
32022    -73.980756                 NaN   690.0     18026.25  211.71  0.306826  
32023    -71.113293                 NaN   614.0  134147.7806  156.47  0.254837  
32024    -79.627933             1404.00   180.0  27798.95621  126.52  0.702889  

[32025 rows x 21 columns]

In [101]:
merged.to_csv('Merged_data_v2.csv', index = False)